### UFABC - Visualização de Dados e Informações - 2023.1
-------------------

## **Prática 07**

### Adinan Alves de Brito Filho
### Priscila Mizukami

In [4]:
import pandas as pd
import requests
import plotly.graph_objects as go

In [5]:
df_airports_columns = ['Airport ID', 'Name', 'City', 'Country', 'IATA', 'ICAO', 'Latitude', 'Longitude', 'Altitude', 'Timezone', 'Daylight Savings Time', 'Tz database time zone', 'Type', 'Source']

df_airports = pd.read_csv('https://raw.githubusercontent.com/jpatokal/openflights/master/data/airports.dat', header=None, names=df_airports_columns)
df_airports.head()

Airport ID                                         Name          City   
0           1                               Goroka Airport        Goroka  \
1           2                               Madang Airport        Madang   
2           3                 Mount Hagen Kagamuga Airport   Mount Hagen   
3           4                               Nadzab Airport        Nadzab   
4           5  Port Moresby Jacksons International Airport  Port Moresby   

            Country IATA  ICAO  Latitude   Longitude  Altitude Timezone   
0  Papua New Guinea  GKA  AYGA -6.081690  145.391998      5282       10  \
1  Papua New Guinea  MAG  AYMD -5.207080  145.789001        20       10   
2  Papua New Guinea  HGU  AYMH -5.826790  144.296005      5388       10   
3  Papua New Guinea  LAE  AYNZ -6.569803  146.725977       239       10   
4  Papua New Guinea  POM  AYPY -9.443380  147.220001       146       10   

  Daylight Savings Time Tz database time zone     Type       Source  
0                     U  Pacific/Port_Moresby  airport  OurAirports  
1                     U  Pacific/Port_Moresby  airport  OurAirports  
2                     U  Pacific/Port_Moresby  airport  OurAirports  
3                     U  Pacific/Port_Moresby  airport  OurAirports  
4                     U  Pacific/Port_Moresby  airport  OurAirports

In [6]:
df_routes_columns = ['Airline', 'Airline ID', 'Source airport', 'Source airport ID', 'Destination airport', 'Destination airport ID', 'Codeshare', 'Stops', 'Equipment']

df_routes = pd.read_csv('https://raw.githubusercontent.com/jpatokal/openflights/master/data/routes.dat', header=None, names=df_routes_columns)
df_routes.head()

Airline Airline ID Source airport Source airport ID Destination airport   
0      2B        410            AER              2965                 KZN  \
1      2B        410            ASF              2966                 KZN   
2      2B        410            ASF              2966                 MRV   
3      2B        410            CEK              2968                 KZN   
4      2B        410            CEK              2968                 OVB   

  Destination airport ID Codeshare  Stops Equipment  
0                   2990       NaN      0       CR2  
1                   2990       NaN      0       CR2  
2                   2962       NaN      0       CR2  
3                   2990       NaN      0       CR2  
4                   4078       NaN      0       CR2

In [7]:
df_routes_with_distance = df_routes.merge(df_airports[['IATA', 'Latitude', 'Longitude']], how='left', left_on='Source airport', right_on='IATA').rename(columns={'IATA': 'Source IATA','Latitude': 'Source Latitude', 'Longitude': 'Source Longitude'})

df_routes_with_distance = df_routes_with_distance.merge(df_airports[['IATA', 'Latitude', 'Longitude']], how='left', left_on='Destination airport', right_on='IATA').rename(columns={'IATA': 'Destination IATA', 'Latitude': 'Destination Latitude', 'Longitude': 'Destination Longitude'})

df_routes_with_distance.drop(['Source IATA', 'Destination IATA'], axis=1, inplace=True)
df_routes_with_distance.dropna(subset=['Source Latitude', 'Source Longitude', 'Destination Latitude', 'Destination Longitude'], inplace=True)

df_routes_with_distance

Airline Airline ID Source airport Source airport ID Destination airport   
0          2B        410            AER              2965                 KZN  \
1          2B        410            ASF              2966                 KZN   
2          2B        410            ASF              2966                 MRV   
3          2B        410            CEK              2968                 KZN   
4          2B        410            CEK              2968                 OVB   
...       ...        ...            ...               ...                 ...   
67658      ZL       4178            WYA              6334                 ADL   
67659      ZM      19016            DME              4029                 FRU   
67660      ZM      19016            FRU              2912                 DME   
67661      ZM      19016            FRU              2912                 OSS   
67662      ZM      19016            OSS              2913                 FRU   

      Destination airport ID Codeshare  Stops Equipment  Source Latitude   
0                       2990       NaN      0       CR2        43.449902  \
1                       2990       NaN      0       CR2        46.283298   
2                       2962       NaN      0       CR2        46.283298   
3                       2990       NaN      0       CR2        55.305801   
4                       4078       NaN      0       CR2        55.305801   
...                      ...       ...    ...       ...              ...   
67658                   3341       NaN      0       SF3       -33.058899   
67659                   2912       NaN      0       734        55.408798   
67660                   4029       NaN      0       734        43.061298   
67661                   2913       NaN      0       734        43.061298   
67662                   2912       NaN      0       734        40.609001   

       Source Longitude  Destination Latitude  Destination Longitude  
0             39.956600             55.606201              49.278702  
1             48.006302             55.606201              49.278702  
2             48.006302             44.225101              43.081902  
3             61.503300             55.606201              49.278702  
4             61.503300             55.012600              82.650703  
...                 ...                   ...                    ...  
67658        137.514008            -34.945000             138.531006  
67659         37.906300             43.061298              74.477600  
67660         74.477600             55.408798              37.906300  
67661         74.477600             40.609001              72.793297  
67662         72.793297             43.061298              74.477600  

[66934 rows x 13 columns]

### Cálculo da distância entre os aeroportos em Km

In [8]:
from geopy.distance import geodesic

def calculate_geodesic_distance(lat1, lon1, lat2, lon2):
    point1 = (lat1, lon1)
    point2 = (lat2, lon2)

    distance = geodesic(point1, point2).km
    return distance

df_routes_with_distance['Geodesic Distance WGS-84'] = df_routes_with_distance.apply(
    lambda row: calculate_geodesic_distance(
        row['Source Latitude'], row['Source Longitude'], 
        row['Destination Latitude'], row['Destination Longitude']), 
    axis=1)

df_routes_with_distance

Airline Airline ID Source airport Source airport ID Destination airport   
0          2B        410            AER              2965                 KZN  \
1          2B        410            ASF              2966                 KZN   
2          2B        410            ASF              2966                 MRV   
3          2B        410            CEK              2968                 KZN   
4          2B        410            CEK              2968                 OVB   
...       ...        ...            ...               ...                 ...   
67658      ZL       4178            WYA              6334                 ADL   
67659      ZM      19016            DME              4029                 FRU   
67660      ZM      19016            FRU              2912                 DME   
67661      ZM      19016            FRU              2912                 OSS   
67662      ZM      19016            OSS              2913                 FRU   

      Destination airport ID Codeshare  Stops Equipment  Source Latitude   
0                       2990       NaN      0       CR2        43.449902  \
1                       2990       NaN      0       CR2        46.283298   
2                       2962       NaN      0       CR2        46.283298   
3                       2990       NaN      0       CR2        55.305801   
4                       4078       NaN      0       CR2        55.305801   
...                      ...       ...    ...       ...              ...   
67658                   3341       NaN      0       SF3       -33.058899   
67659                   2912       NaN      0       734        55.408798   
67660                   4029       NaN      0       734        43.061298   
67661                   2913       NaN      0       734        43.061298   
67662                   2912       NaN      0       734        40.609001   

       Source Longitude  Destination Latitude  Destination Longitude   
0             39.956600             55.606201              49.278702  \
1             48.006302             55.606201              49.278702   
2             48.006302             44.225101              43.081902   
3             61.503300             55.606201              49.278702   
4             61.503300             55.012600              82.650703   
...                 ...                   ...                    ...   
67658        137.514008            -34.945000             138.531006   
67659         37.906300             43.061298              74.477600   
67660         74.477600             55.408798              37.906300   
67661         74.477600             40.609001              72.793297   
67662         72.793297             43.061298              74.477600   

       Geodesic Distance WGS-84  
0                   1507.989680  
1                   1040.943207  
2                    449.036664  
3                    773.126239  
4                   1343.161122  
...                         ...  
67658                229.334786  
67659               2949.906099  
67660               2949.906099  
67661                306.189294  
67662                306.189294  

[66934 rows x 14 columns]

In [9]:
data = requests.get('https://www.eurocontrol.int/performance/data/download/xls/Airport_Traffic.xlsx')

df_airport_traffic = pd.read_excel(data.content, sheet_name='DATA')
df_airport_traffic.head()

YEAR  MONTH_NUM MONTH_MON   FLT_DATE APT_ICAO       APT_NAME STATE_NAME   
0  2016          1       JAN 2016-01-01     EBAW        Antwerp    Belgium  \
1  2016          1       JAN 2016-01-01     EBBR       Brussels    Belgium   
2  2016          1       JAN 2016-01-01     EBCI      Charleroi    Belgium   
3  2016          1       JAN 2016-01-01     EBLG          Liège    Belgium   
4  2016          1       JAN 2016-01-01     EBOS  Ostend-Bruges    Belgium   

   FLT_DEP_1  FLT_ARR_1  FLT_TOT_1  FLT_DEP_IFR_2  FLT_ARR_IFR_2   
0          4          3          7            NaN            NaN  \
1        174        171        345          174.0          161.0   
2         45         47         92           45.0           45.0   
3          6          7         13            NaN            NaN   
4          7          7         14            NaN            NaN   

   FLT_TOT_IFR_2           Pivot Label  
0            NaN        Antwerp (EBAW)  
1          335.0       Brussels (EBBR)  
2           90.0      Charleroi (EBCI)  
3            NaN          Liège (EBLG)  
4            NaN  Ostend-Bruges (EBOS)

In [10]:
# Adicionando uma coluna com o código IATA de cada aeroporto
df_airport_traffic = df_airport_traffic.merge(df_airports[['IATA', 'ICAO']], how='left', left_on='APT_ICAO', right_on='ICAO')

# Removendo a coluna do código ICAO dos aeroportos
df_airport_traffic.drop('ICAO',axis=1, inplace=True)

In [11]:
# Criando uma cópia para preservar o dataframe original
df_airport_traffic_copy = df_airport_traffic.copy(deep=True)

# Numero de entradas
print(len(df_airport_traffic_copy.index))

# Removendo as entradas com código IATA em branco
df_airport_traffic_copy.dropna(subset=['IATA'], inplace=True)

# Removendo as linhas com código IATA inválido
df_airport_traffic_copy = df_airport_traffic_copy[df_airport_traffic_copy.IATA != '\\N']

# Numero de entradas após limpeza dos dados
print(len(df_airport_traffic_copy.index))

764508
749154


In [12]:
# Removendo as colunas que não serão utilizadas
df_airport_traffic_copy = df_airport_traffic_copy.drop(['FLT_DATE','APT_ICAO','FLT_DEP_1','FLT_ARR_1','FLT_DEP_IFR_2','FLT_ARR_IFR_2','Pivot Label','FLT_TOT_IFR_2', 'MONTH_NUM', 'MONTH_MON', 'APT_NAME', 'STATE_NAME'],axis=1)

In [13]:
# Exibindo primeiro ano em que os dados foram colhidos por aeroporto
# Exemplo: O primeiro ano de monitoramento foi 2016 para 269 aeroportos
print(df_airport_traffic_copy.groupby('IATA')['YEAR'].min().value_counts())
print('\n')

# Exibindo o percentual do ano de início de monitoramento
print(df_airport_traffic_copy.groupby('IATA')['YEAR'].min().value_counts(normalize=True) * 100
)
print("\nPara que a VIS esteja correta, devemos comparar apenas os aeroportos cujos dados foram colhidos no mesmo intervalo de tempo.\nPor isso, vamos considerar o intervalo de 2018 a 2023 e desprezar os aeroportos cujo monitoramento iniciou após 2018.")

YEAR
2016    269
2018     47
2019      2
2021      2
Name: count, dtype: int64


YEAR
2016    84.0625
2018    14.6875
2019     0.6250
2021     0.6250
Name: proportion, dtype: float64

Para que a VIS esteja correta, devemos comparar apenas os aeroportos cujos dados foram colhidos no mesmo intervalo de tempo.
Por isso, vamos considerar o intervalo de 2018 a 2023 e desprezar os aeroportos cujo monitoramento iniciou após 2018.


In [14]:
# Mantendo apenas os dados a partir de 2018 e removendo as entradas que não possuem dados em 2018
df_airport_traffic_copy = df_airport_traffic_copy.query('YEAR >= 2018').groupby('IATA').filter(lambda x: x['YEAR'].min() == 2018)

# Somando as entradas e saídas em cada aeroporto no intervalo 2018-2023 
df_airport_traffic_grouped = df_airport_traffic_copy.groupby('IATA')[['FLT_TOT_1']].count().reset_index()

# Renomeando coluna do tráfego entre 2018-2023 para TOTAL_FLIGHTS
df_airport_traffic_grouped = df_airport_traffic_grouped.rename(columns={"FLT_TOT_1": "TOTAL_FLIGHTS"})
df_airport_traffic_grouped.head(5)


IATA  TOTAL_FLIGHTS
0  ABC           1045
1  ABZ           1857
2  ACE           1857
3  ADB           1848
4  AES           1857

In [15]:
# Criando uma cópia do dataframe com as rotas e suas distâncias
df = df_routes_with_distance.copy(deep=True)

# Removendo as colunas que não serão utilizadas
df = df.drop(['Airline','Airline ID', 'Source airport ID', 'Destination airport ID','Codeshare', 'Stops', 'Equipment'],axis=1)

# Removendo entradas duplicadas (Diferentes companhias aereas não nos interessam)
df.drop_duplicates(inplace=True)

In [16]:
# Adicionando uma coluna para a quantidade total de voos no aeroporto de origem
df = df.merge(df_airport_traffic_grouped[['IATA', 'TOTAL_FLIGHTS']], how='left', left_on='Source airport', right_on='IATA').rename(columns={'IATA': 'Source IATA','TOTAL_FLIGHTS': 'Source Total Flights'})

# Removendo coluna que não será utilizada
df = df.drop(['Source IATA'], axis=1, inplace=False)

# Removendo os dados em branco
df = df.dropna()

### Cálculo do fator custo para os aeroportos de origem

In [17]:
# Cálculo do fator custo para os aeroportos de origem
df['Source Cost O'] = df['Source Total Flights']/df['Geodesic Distance WGS-84']

# Restaurando o índice do DF e padronizando os nomes das colunas
df.reset_index(drop=True, inplace=True)
df.columns = ['S_AIRPORT', 'D_AIRPORT', 'S_LAT', 'S_LON', 'D_LAT', 'D_LON', 'DISTANCE_WGS-84', 'S_TOTAL_TRAFFIC', 'S_COST']

In [18]:
# Adicionando ao DF o nome, cidade e país do aeroporto de origem
df = df.merge(df_airports[['Name','City','Country','IATA']], how='left', left_on='S_AIRPORT', right_on='IATA').rename(
    columns={
        'Name': 'S_AIRPORT_NAME',
        'City': 'S_CITY',
        'Country': 'S_COUNTRY'
        }
    )
df.drop(['IATA'], axis=1, inplace=True)

# Adicionando ao DF o nome, cidade e país do aeroporto de destino
df = df.merge(df_airports[['Name','City','Country','IATA']], how='left', left_on='D_AIRPORT', right_on='IATA').rename(
    columns={
        'Name': 'D_AIRPORT_NAME',
        'City': 'D_CITY',
        'Country': 'D_COUNTRY'
        }
    )
df.drop(['IATA'], axis=1, inplace=True)

### Dataframe final com dados tratados e prontos para o plot

In [19]:
df_completo = df.copy()

# Mantendo apenas as entradas onde o país de origem é diferente do país de destino
df = df[df['D_COUNTRY'] != df['S_COUNTRY']]

# Média do custo dos aeroportos de origem para cada rota
sum_cost_source = df.groupby(['S_AIRPORT','S_LAT', 'S_LON', 'S_AIRPORT_NAME', 'S_COUNTRY'])[['S_COST']].mean().reset_index()

## Questão 1

In [20]:
# Código adaptado de https://coderzcolumn.com/tutorials/data-science/how-to-create-connection-map-chart-in-python-jupyter-notebook-plotly-and-geopandas

fig = go.Figure()

df_flights = zip(df['S_LAT'], df['D_LAT'], df['S_LON'], df['D_LON'])

# Loop para cada entrada do dataframe, para adicionar uma linha entre a origem e o destino
for s_lat, d_lat, s_lon, d_lon in df_flights:
    fig.add_trace(
        go.Scattergeo(
            lat = [s_lat, d_lat],
            lon = [s_lon, d_lon],
            mode = 'lines', 
            line = dict(width = 0.1, color='red')
            ))

# Criando os rótulos dos pontos do plot
airports = sum_cost_source['S_AIRPORT_NAME'].values.tolist()
countries = sum_cost_source['S_COUNTRY'].values.tolist()
data_labels = [airport + " : "+ country for airport, country in zip(airports, countries)]

fig.add_trace(go.Scattergeo(
    lon = sum_cost_source['S_LON'].values.tolist(),
    lat = sum_cost_source['S_LAT'].values.tolist(),
    hoverinfo = 'text', text = data_labels, mode = 'markers',
    marker = dict(size = sum_cost_source['S_COST'].values*3, color = 'blue', opacity=0.5)))

# Alterando o layout do gráfico
fig.update_layout(
    #title_text='Rotas de voos internacionais , com o fator de custo dos aeroportos de origem<br><sup>Maior o fator de custo, maior o círculo</sup>',
    title_text='Fator de custo dos aeroportos de origem em rotas internacionais<br><sup>Maior o fator de custo, maior o círculo</sup>',
    #title_text='Rotas de voos internacionais entre 01/2018 e 03/2023.<br><sup>Os círculos azuis representam o fator custo dos aeroportos de origem. Quanto maior o círculo, maior o fator custo.</sup>',
    height=675, width=1200, margin={'t':60,'b':20,'l':10, 'r':10, 'pad':0},
    showlegend=False,
    paper_bgcolor="white",
    title_font_family="Helvetica",
    geo=dict(showland=True, landcolor='#DFE7F4', bgcolor='white', coastlinewidth=0))

#fig.write_image("q1_v2.png")
fig.show()

## Questão 2

In [21]:
df_brazil_airports = df_airports[df_airports.Country == 'Brazil'].copy(deep=True)
df_brazil_airports.drop(df_brazil_airports[df_brazil_airports.City == 'CONSELVAN'].index.to_list(), inplace=True)
df_brazil_airports

Airport ID                                  Name                   City   
2392        2518         Conceição do Araguaia Airport  Conceicao Do Araguaia  \
2393        2519  Campo Délio Jardim de Mattos Airport         Rio De Janeiro   
2394        2520                         Amapá Airport                  Amapa   
2395        2521                    Araraquara Airport             Araracuara   
2396        2522                   Santa Maria Airport                Aracaju   
...          ...                                   ...                    ...   
7643       13723                Augusto Severo Airport                  Natal   
7647       13735                        Flores Airport                 MANAUS   
7659       13772               Fazenda Uiapuru Airport               COMODORO   
7670       13830              Fazenda Kajussol Airport  Alta Floresta D'Oeste   
7672       13881                 Costa Marques Airport          COSTA MARQUES   

     Country IATA  ICAO   Latitude  Longitude  Altitude Timezone   
2392  Brazil  CDJ  SBAA  -8.348350 -49.301498       653       -3  \
2393  Brazil   \N  SBAF -22.875099 -43.384701       110       -3   
2394  Brazil   \N  SBAM   2.077510 -50.858200        45       -3   
2395  Brazil  AQA  SBAQ -21.812000 -48.132999      2334       -3   
2396  Brazil  AJU  SBAR -10.984000 -37.070301        23       -3   
...      ...  ...   ...        ...        ...       ...      ...   
7643  Brazil   \N  SBNT  -5.911420 -35.247700       169       \N   
7647  Brazil   \N  SWFN  -3.072778 -60.021111       203       -4   
7659  Brazil   \N  SWVJ -13.663889 -56.002220      1519       -4   
7670  Brazil   \N  SJYD -11.964722 -61.686668       636       -4   
7672  Brazil  CQS  SWCQ -12.421100 -64.251602       555       -4   

     Daylight Savings Time Tz database time zone     Type       Source  
2392                     S         America/Belem  airport  OurAirports  
2393                     S     America/Sao_Paulo  airport  OurAirports  
2394                     S     America/Fortaleza  airport  OurAirports  
2395                     S     America/Sao_Paulo  airport  OurAirports  
2396                     S     America/Fortaleza  airport  OurAirports  
...                    ...                   ...      ...          ...  
7643                    \N                    \N  airport  OurAirports  
7647                     S                    \N  airport  OurAirports  
7659                     S                    \N  airport  OurAirports  
7670                     S                    \N  airport  OurAirports  
7672                     S                    \N  airport  OurAirports  

[263 rows x 14 columns]

In [22]:
# Obtendo IDs dos aeroportos do Brasil no formato string
brazil_airports_IDs = [str(airport) for airport in df_brazil_airports['Airport ID'].unique()]

# Filtrando rotas nacionais do Brasil a partir do ID do aeroporto
df_br_routes_ID = df_routes_with_distance.loc[
    df_routes_with_distance['Source airport ID'].isin(brazil_airports_IDs) & 
    df_routes_with_distance['Destination airport ID'].isin(brazil_airports_IDs)].copy()

# Filtrando rotas nacionais do Brasil a partir do IATA do aeroporto
df_br_routes_IATA = df_routes_with_distance.loc[
    df_routes_with_distance['Source airport'].isin(df_brazil_airports.IATA.unique()) & 
    df_routes_with_distance['Destination airport'].isin(df_brazil_airports.IATA.unique())].copy()

# Obtendo a intersecção entre as duas filtragens
if len(df_br_routes_IATA.index.to_list()) > len(df_br_routes_ID.index.to_list()):
    print("Dataframe filtrado via IATA é maior.")
    indices_br_routes = df_br_routes_IATA.index.to_list()
else:
    print("Dataframe filtrado via ID é maior.")
    indices_br_routes = df_br_routes_ID.index.to_list()

Dataframe filtrado via IATA é maior.


In [23]:
intersecao = list(set(df_br_routes_IATA.index.to_list()) & set(df_br_routes_ID.index.to_list()))
for item in intersecao:
    indices_br_routes.remove(item)

print('O Dataframe das rotas do Brasil cujo rotas foram filtradas via IATA possuem mais linhas pois as seguintes rotas tem como ID de origem ou destino o caractere \ N:')
print(indices_br_routes)

O Dataframe das rotas do Brasil cujo rotas foram filtradas via IATA possuem mais linhas pois as seguintes rotas tem como ID de origem ou destino o caractere \ N:
[8638, 8741, 8742, 8841, 39948, 39950, 39951, 39952, 39954]


In [24]:
df_br_routes_IATA.columns = [str(item).upper().replace(" ", "_") for item in df_br_routes_IATA.columns.to_list()]
df_br_routes_IATA.head()

AIRLINE AIRLINE_ID SOURCE_AIRPORT SOURCE_AIRPORT_ID DESTINATION_AIRPORT   
214      2Z       1729            AUX              7376                 PMW  \
215      2Z       1729            BRA              7373                 BSB   
216      2Z       1729            BRA              7373                 SSA   
217      2Z       1729            BSB              2531                 BRA   
218      2Z       1729            BSB              2531                 OPS   

    DESTINATION_AIRPORT_ID CODESHARE  STOPS EQUIPMENT  SOURCE_LATITUDE   
214                   4214       NaN      0       AT7        -7.227870  \
215                   2531       NaN      0       AT7       -12.078900   
216                   2621       NaN      0       AT7       -12.078900   
217                   7373       NaN      0       AT7       -15.869167   
218                   7367       NaN      0       AT7       -15.869167   

     SOURCE_LONGITUDE  DESTINATION_LATITUDE  DESTINATION_LONGITUDE   
214        -48.240501            -10.291500             -48.356998  \
215        -45.008999            -15.869167             -47.920834   
216        -45.008999            -12.908611             -38.322498   
217        -47.920834            -12.078900             -45.008999   
218        -47.920834            -11.885000             -55.586109   

     GEODESIC_DISTANCE_WGS-84  
214                339.080666  
215                524.207952  
216                732.571935  
217                524.207952  
218                938.304127

In [25]:
fig = go.Figure()

brazil_flights = zip(
    df_br_routes_IATA['SOURCE_LATITUDE'], df_br_routes_IATA['DESTINATION_LATITUDE'], 
    df_br_routes_IATA['SOURCE_LONGITUDE'], df_br_routes_IATA['DESTINATION_LONGITUDE'])

# Loop para cada entrada do dataframe, para adicionar uma linha entre a origem e o destino
for s_lat, d_lat, s_lon, d_lon in brazil_flights:
    fig.add_trace(
        go.Scattergeo(
            lat = [s_lat, d_lat],
            lon = [s_lon, d_lon],
            mode = 'lines', 
            line = dict(width = 0.1, color='red')
            ))

# Criando os rótulos dos pontos do plot
airports = [str(item).title() for item in df_brazil_airports['Name'].values.tolist()]
cities = [str(item).title() for item in df_brazil_airports['City'].values.tolist()]
data_labels = [airports + " : "+ city for airports,city in zip(airports, cities)]

fig.add_trace(
    go.Scattergeo(
    lon = df_brazil_airports['Longitude'].values.tolist(),
    lat = df_brazil_airports['Latitude'].values.tolist(),
    hoverinfo = 'text', 
    text = data_labels, 
    mode = 'markers',
    marker = dict(size = 4, color = 'blue', opacity=1)))

# Alterando o layout do gráfico
fig.update_layout(
    title_text='Aeroportos do Brasil e suas rotas domésticas',
    height=600, width=500, margin={'t':60,'b':10,'l':0, 'r':50, 'pad':0},
    showlegend=False,
    paper_bgcolor="white",
    title_font_family="Helvetica",
    geo = dict(projection_type='natural earth', scope='south america', countrywidth=0.3, landcolor='#DFE7F4'))

fig.write_image("q2_v1.png")
fig.show()

In [55]:
fig = go.Figure()

brazil_flights = zip(
    df_br_routes_IATA['SOURCE_LATITUDE'], df_br_routes_IATA['DESTINATION_LATITUDE'], 
    df_br_routes_IATA['SOURCE_LONGITUDE'], df_br_routes_IATA['DESTINATION_LONGITUDE'])

# Loop para cada entrada do dataframe, para adicionar uma linha entre a origem e o destino
for s_lat, d_lat, s_lon, d_lon in brazil_flights:
    fig.add_trace(
        go.Scattergeo(
            lat = [s_lat, d_lat],
            lon = [s_lon, d_lon],
            mode = 'lines', 
            line = dict(width = 0.08, color='red')
            ))

# Criando os rótulos dos pontos do plot
airports = [str(item).title() for item in df_brazil_airports['Name'].values.tolist()]
cities = [str(item).title() for item in df_brazil_airports['City'].values.tolist()]
data_labels = [airports + " : "+ city for airports,city in zip(airports, cities)]

fig.add_trace(
    go.Scattergeo(
    lon = df_brazil_airports['Longitude'].values.tolist(),
    lat = df_brazil_airports['Latitude'].values.tolist(),
    hoverinfo = 'text', 
    text = data_labels, 
    mode = 'markers',
    marker = dict(size = 3, color = 'blue', opacity=1)))

# Alterando o layout do gráfico
fig.update_layout(
    title_text='Aeroportos do Brasil e suas rotas domésticas',
    height=600, width=500, margin={'t':60,'b':10,'l':0, 'r':50, 'pad':0},
    showlegend=False,
    paper_bgcolor="LightBlue",
    title_font_family="Helvetica",
    geo = dict(resolution=50,projection_type='natural earth', scope='south america', countrywidth=0.3, 
    showland=True, landcolor="LightGreen", bgcolor="LightBlue", showlakes=False, showrivers=False))
    
#fig.write_image("q2_v2_min.png")
fig.show()